In [1]:
def all_files(list_file):
    file_names = []
    with open(list_file, 'rb') as f:
        for line in f:
            file_names.append(line.split()[0])
    return file_names

In [60]:
train_files = all_files('/Users/ecsark/Documents/visualdb/project/wikiart/train.txt')
test_files = all_files('/Users/ecsark/Documents/visualdb/project/wikiart/test.txt')
modified_dir = '/Users/ecsark/Documents/visualdb/project/wikiart/images-512/'
noise_dir = '/Users/ecsark/Documents/visualdb/project/wikiart/images-noise/'
bright_dir = '/Users/ecsark/Documents/visualdb/project/wikiart/images-bright/'
dark_dir = '/Users/ecsark/Documents/visualdb/project/wikiart/images-dark/'

In [3]:
from PIL import Image
def resize_and_crop(img_path, modified_path, size, crop_type='top'):
    """
    Resize and crop an image to fit the specified size.

    args:
    img_path: path for the image to resize.
    modified_path: path to store the modified image.
    size: `(width, height)` tuple.
    crop_type: can be 'top', 'middle' or 'bottom', depending on this
    value, the image will cropped getting the 'top/left', 'middle' or
    'bottom/right' of the image to fit the size.
    raises:
    Exception: if can not open the file in img_path of there is problems
    to save the image.
    ValueError: if an invalid `crop_type` is provided.
    """
    # If height is higher we resize vertically, if not we resize horizontally
    img = Image.open(img_path)
    # Get current and desired ratio for the images
    img_ratio = img.size[0] / float(img.size[1])
    ratio = size[0] / float(size[1])
    #The image is scaled/cropped vertically or horizontally depending on the ratio
    if ratio > img_ratio:
        img = img.resize((size[0], int(round(size[0] * img.size[1] / img.size[0]))),
            Image.ANTIALIAS)
        # Crop in the top, middle or bottom
        if crop_type == 'top':
            box = (0, 0, img.size[0], size[1])
        elif crop_type == 'middle':
            box = (0, int(round((img.size[1] - size[1]) / 2)), img.size[0],
                int(round((img.size[1] + size[1]) / 2)))
        elif crop_type == 'bottom':
            box = (0, img.size[1] - size[1], img.size[0], img.size[1])
        else :
            raise ValueError('ERROR: invalid value for crop_type')
        img = img.crop(box)
    elif ratio < img_ratio:
        img = img.resize((int(round(size[1] * img.size[0] / img.size[1])), size[1]),
            Image.ANTIALIAS)
        # Crop in the top, middle or bottom
        if crop_type == 'top':
            box = (0, 0, size[0], img.size[1])
        elif crop_type == 'middle':
            box = (int(round((img.size[0] - size[0]) / 2)), 0,
                int(round((img.size[0] + size[0]) / 2)), img.size[1])
        elif crop_type == 'bottom':
            box = (img.size[0] - size[0], 0, img.size[0], img.size[1])
        else :
            raise ValueError('ERROR: invalid value for crop_type')
        img = img.crop(box)
    else :
        img = img.resize((size[0], size[1]),
            Image.ANTIALIAS)
    # If the scale is the same, we do not need to crop
    img.save(modified_path)

In [8]:
def resize(img_path, modified_path, smaller_dim):
    
    img = Image.open(img_path)
    
    img_ratio = img.size[0] / float(img.size[1])
    
    if img.size[0] > img.size[1] > smaller_dim:
        img = img.resize((int(smaller_dim*img_ratio), smaller_dim), Image.ANTIALIAS)
    
    if img.size[1] > img.size[0] > smaller_dim:
        img = img.resize((smaller_dim, int(smaller_dim/img_ratio)), Image.ANTIALIAS)
    img.save(modified_path)

In [10]:
print modified_dir + test_files[0].split('/')[-1]

/Users/ecsark/Documents/visualdb/project/wikiart/modified/egon-schiele_seated-girl-1910.jpg


In [13]:
for tf in train_files:
    modified_path = modified_dir + tf.split('/')[-1]
    print modified_path
    resize(tf, modified_path, 512)   

/Users/ecsark/Documents/visualdb/project/wikiart/modified/nicholas-roerich_the-way.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/modified/nicholas-roerich_the-way.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/modified/carl-larsson_the-verandah.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/modified/carl-larsson_the-verandah.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/modified/max-weber_the-muses.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/modified/max-weber_the-muses.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/modified/vincent-van-gogh_fishing-boats-at-sea-1888.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/modified/vincent-van-gogh_fishing-boats-at-sea-1888.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/modified/martiros-saryan_blue-flowers-1914.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/modified/martiros-saryan_blue-flowers-1914.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/modified/francisco-toledo_toro-1965

In [22]:
import scipy.misc
import numpy

def make_noise(filename, modified_file, lam):
    imagea = (scipy.misc.imread(filename)).astype(float)
    poissonNoise = numpy.random.poisson(lam,imagea.shape).astype(float)
    noisyImage = imagea + poissonNoise
    scipy.misc.imsave(modified_file, noisyImage)

In [30]:
for tf in train_files:
    shrinked_orginal = modified_dir + tf.split('/')[-1]
    new_path = noise_dir + tf.split('/')[-1]
    print new_path
    make_noise(shrinked_orginal, new_path, 4.0)   

/Users/ecsark/Documents/visualdb/project/wikiart/images-noise/nicholas-roerich_the-way.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-noise/carl-larsson_the-verandah.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-noise/max-weber_the-muses.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-noise/vincent-van-gogh_fishing-boats-at-sea-1888.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-noise/martiros-saryan_blue-flowers-1914.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-noise/francisco-toledo_toro-1965.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-noise/cuno-amiet_bauerngarten-1918.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-noise/theodore-rousseau_last-houses-of-port-en-bessin-calvados.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-noise/ernst-ludwig-kirchner_two-cocottes.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-noise/mary-cassatt_sara-in-a-bonnet.jpg
/Users/ecsark/

In [33]:

image = Image.open(train_files[2])
image.show()

In [48]:
contrast = ImageEnhance.Brightness(image)
contrast.enhance(0.9).show()

In [47]:
image.show()

In [56]:
from PIL import Image, ImageEnhance
def make_bright(filename, modified_file, val):
    image = Image.open(filename)
    contrast = ImageEnhance.Brightness(image)
    contrast.enhance(val).save(modified_file)

In [58]:
for tf in train_files:
    shrinked_orginal = modified_dir + tf.split('/')[-1]
    bright_path = bright_dir + tf.split('/')[-1]
    print bright_path
    make_bright(shrinked_orginal, bright_path, 1.15) 

/Users/ecsark/Documents/visualdb/project/wikiart/images-bright/nicholas-roerich_the-way.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-bright/carl-larsson_the-verandah.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-bright/max-weber_the-muses.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-bright/vincent-van-gogh_fishing-boats-at-sea-1888.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-bright/martiros-saryan_blue-flowers-1914.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-bright/francisco-toledo_toro-1965.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-bright/cuno-amiet_bauerngarten-1918.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-bright/theodore-rousseau_last-houses-of-port-en-bessin-calvados.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-bright/ernst-ludwig-kirchner_two-cocottes.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-bright/mary-cassatt_sara-in-a-bonnet.jpg
/Use

In [62]:
for tf in train_files + test_files:
    shrinked_orginal = modified_dir + tf.split('/')[-1]
    dark_path = dark_dir + tf.split('/')[-1]
    print dark_path
    make_bright(shrinked_orginal, dark_path, 0.86) 

/Users/ecsark/Documents/visualdb/project/wikiart/images-dark/nicholas-roerich_the-way.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-dark/carl-larsson_the-verandah.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-dark/max-weber_the-muses.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-dark/vincent-van-gogh_fishing-boats-at-sea-1888.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-dark/martiros-saryan_blue-flowers-1914.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-dark/francisco-toledo_toro-1965.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-dark/cuno-amiet_bauerngarten-1918.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-dark/theodore-rousseau_last-houses-of-port-en-bessin-calvados.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-dark/ernst-ludwig-kirchner_two-cocottes.jpg
/Users/ecsark/Documents/visualdb/project/wikiart/images-dark/mary-cassatt_sara-in-a-bonnet.jpg
/Users/ecsark/Documents/